In [54]:
pip install xgboost

  Obtaining dependency information for xgboost from https://files.pythonhosted.org/packages/45/6d/8c1d2570a52db6263d855c3ee3daf8f4bdf4a365cd6610772d6fce5fd904/xgboost-2.0.3-py3-none-macosx_10_15_x86_64.macosx_11_0_x86_64.macosx_12_0_x86_64.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 14.5 MB/s eta 0:00:0000:0100:01
Note: you may need to restart the kernel to use updated packages.


In [1]:
import numpy as np 
import pandas as pd

from sklearn.model_selection import KFold, cross_val_score

# models import
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import Lasso
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor, GradientBoostingRegressor,AdaBoostRegressor
from sklearn.neural_network import MLPRegressor
from xgboost import XGBRegressor


from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler, OrdinalEncoder
from sklearn.compose import ColumnTransformer
from sklearn.svm import SVR


from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error

from sklearn.decomposition import PCA


/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


In [2]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

- First of all upload  gurgaon_properties_post_feature_selection_v2.csv') File.

- In this file already converted back all categorical column to  categorical which in process converted numeric.

- Because converting from categorical to numeric will do in pipeline as this pipeline will help to convert further data too when it receive on direct in market.


In [3]:
df = pd.read_csv('gurgaon_properties_post_feature_selection_v2.csv')

In [4]:
df.head()

property_type      sector  price  bedRoom  bathroom balcony   agePossession  \
0          flat   sector 36   0.82      3.0       2.0       2    New Property   
1          flat   sector 89   0.95      2.0       2.0       2    New Property   
2          flat  sohna road   0.32      2.0       2.0       1    New Property   
3          flat   sector 92   1.60      3.0       4.0      3+  Relatively New   
4          flat  sector 102   0.48      2.0       2.0       1  Relatively New   

   built_up_area  servant room  store room  furnishing_type luxury_category  \
0          850.0           0.0         0.0              0.0             Low   
1         1226.0           1.0         0.0              0.0             Low   
2         1000.0           0.0         0.0              0.0             Low   
3         1615.0           1.0         0.0              1.0            High   
4          582.0           0.0         1.0              0.0            High   

  floor_category  
0      Low Floor  
1      Mid Floor  
2     High Floor  
3      Mid Floor  
4      Mid Floor

In [5]:
df['furnishing_type'].value_counts()

furnishing_type
0.0    2349
1.0    1018
2.0     187
Name: count, dtype: int64

In [6]:
# 0 -> unfurnished
# 1 -> semifurnished
# 2 -> furnished

In [7]:
df['furnishing_type']= df['furnishing_type'].replace({0.0: 'unfurnished', 1.0: 'semifurnished', 2.0: 'furnished'})

In [8]:
df.head()

property_type      sector  price  bedRoom  bathroom balcony   agePossession  \
0          flat   sector 36   0.82      3.0       2.0       2    New Property   
1          flat   sector 89   0.95      2.0       2.0       2    New Property   
2          flat  sohna road   0.32      2.0       2.0       1    New Property   
3          flat   sector 92   1.60      3.0       4.0      3+  Relatively New   
4          flat  sector 102   0.48      2.0       2.0       1  Relatively New   

   built_up_area  servant room  store room furnishing_type luxury_category  \
0          850.0           0.0         0.0     unfurnished             Low   
1         1226.0           1.0         0.0     unfurnished             Low   
2         1000.0           0.0         0.0     unfurnished             Low   
3         1615.0           1.0         0.0   semifurnished            High   
4          582.0           0.0         1.0     unfurnished            High   

  floor_category  
0      Low Floor  
1      Mid Floor  
2     High Floor  
3      Mid Floor  
4      Mid Floor

In [9]:
# Splitting data into X and y
X = df.drop(columns=['price'])
y = df['price']

In [10]:
X

property_type             sector  bedRoom  bathroom balcony  \
0             flat          sector 36      3.0       2.0       2   
1             flat          sector 89      2.0       2.0       2   
2             flat         sohna road      2.0       2.0       1   
3             flat          sector 92      3.0       4.0      3+   
4             flat         sector 102      2.0       2.0       1   
5             flat        gwal pahari      4.0       4.0      3+   
6             flat         sector 108      3.0       3.0      3+   
7             flat         sector 102      3.0       4.0       3   
8            house         sector 105      3.0       2.0       1   
9            house          sector 26      3.0       3.0       2   
10           house         sector 109      3.0       2.0       0   
11            flat          sector 28      2.0       2.0       2   
12            flat         sector 109      3.0       4.0       3   
13            flat          sector 65      4.0       4.0      3+   
14           house          sector 12      2.0       4.0       2   
15            flat          sector 92      3.0       4.0       3   
16            flat          sector 85      2.0       2.0       3   
17            flat         sector 70a      2.0       2.0       3   
18            flat          sector 85      3.0       4.0      3+   
19            flat          sector 30      2.0       2.0       1   
20            flat         sector 107      2.0       2.0      3+   
21            flat           sector 3      2.0       2.0       3   
22            flat           sector 2      1.0       1.0       1   
23           house          sector 41      8.0       5.0      3+   
24           house          sector 41      7.0       7.0      3+   
25            flat          sector 28      4.0       2.0      3+   
26           house           sector 4      1.0       1.0       0   
27           house         sector 109      4.0       4.0      3+   
28            flat          sector 62      2.0       2.0       3   
29           house          sector 49      6.0       6.0       3   
30            flat          sector 81      2.0       2.0       3   
31            flat          sector 65      3.0       3.0       3   
32            flat          sector 66      3.0       3.0       3   
33           house          sector 89      2.0       2.0       2   
34            flat          sector 86      3.0       3.0      3+   
35           house          sector 48      4.0       4.0      3+   
36           house         sector 109      5.0       6.0      3+   
37            flat          sector 51      4.0       4.0       3   
38            flat          sector 37      3.0       3.0       3   
39            flat         sector 111      2.0       2.0       2   
40            flat          sector 67      3.0       3.0       3   
41           house          sector 28      4.0       3.0       3   
42            flat         sector 111      3.0       4.0       2   
43            flat         sector 113      3.0       3.0      3+   
44           house          sector 13      3.0       6.0       2   
45            flat          sector 61      3.0       2.0       3   
46            flat         sector 113      3.0       3.0       3   
47            flat          sector 69      3.0       3.0       1   
48            flat          sector 89      3.0       2.0       0   
49            flat         sector 67a      3.0       4.0       3   
50            flat         sector 37d      2.0       2.0       3   
51            flat          sector 82      2.0       2.0       2   
52            flat          sector 53      3.0       3.0      3+   
53            flat          sector 74      2.0       2.0       3   
54            flat         sector 37d      3.0       3.0       3   
55            flat         sector 108      3.0       4.0       3   
56            flat          sector 52      1.0       1.0       0   
57            flat          sector 12      2.0       2.0     

In [11]:
y

0        0.82
1        0.95
2        0.32
3        1.60
4        0.48
5        7.50
6        2.00
7        1.90
8        1.20
9        4.50
10       1.55
11       1.60
12       2.25
13       2.77
14       1.20
15       1.55
16       1.09
17       1.15
18       1.77
19       0.85
20       0.90
21       1.20
22       0.60
23       9.00
24       7.00
25       0.90
26       0.40
27       5.65
28       2.15
29       4.40
30       0.64
31       2.86
32       3.50
33       0.70
34       1.54
35       8.25
36       6.10
37       2.10
38       1.25
39       0.70
40       2.80
41       5.50
42       2.58
43       3.00
44       1.25
45       2.10
46       2.45
47       1.38
48       1.71
49       1.85
50       0.60
51       0.81
52       5.60
53       1.50
54       1.45
55       1.65
56       0.45
57       0.35
58       5.75
59       1.12
60       0.75
61       0.25
62       0.67
63       0.56
64       1.75
65       4.15
66       3.40
67       2.30
68       7.60
69       0.32
70       0.45
71    

In [12]:
X.shape

(3554, 12)

In [13]:
y.shape

(3554,)

So here apply three type of encoding:

### 1. Ordinal Encoding
### 2. One Hot Encoding
### 3. Target Encoding


- Then train model upon all three encoding and find r2 score
- Then on which encoding technique get best r2score will use for final production.

- Ordinal Encoding works well with "Tree Based Model"
- One Hot Encoding which apply upon Nominal Data works well with "Linear Models"
- Target Encoding works well with "Tree Based Model"


- Where we have "High Dimensionality" feature we use "Target Encoding"




In [14]:
# Applying the log1p transformation to the target variable

In [15]:
y_transformed = np.log1p(y)

In [16]:
y_transformed

0       0.598837
1       0.667829
2       0.277632
3       0.955511
4       0.392042
5       2.140066
6       1.098612
7       1.064711
8       0.788457
9       1.704748
10      0.936093
11      0.955511
12      1.178655
13      1.327075
14      0.788457
15      0.936093
16      0.737164
17      0.765468
18      1.018847
19      0.615186
20      0.641854
21      0.788457
22      0.470004
23      2.302585
24      2.079442
25      0.641854
26      0.336472
27      1.894617
28      1.147402
29      1.686399
30      0.494696
31      1.350667
32      1.504077
33      0.530628
34      0.932164
35      2.224624
36      1.960095
37      1.131402
38      0.810930
39      0.530628
40      1.335001
41      1.871802
42      1.275363
43      1.386294
44      0.810930
45      1.131402
46      1.238374
47      0.867100
48      0.996949
49      1.047319
50      0.470004
51      0.593327
52      1.887070
53      0.916291
54      0.896088
55      0.974560
56      0.371564
57      0.300105
58      1.9095

# Ordinal Enocding

In [17]:
columns_to_encode = ['property_type','sector', 'balcony', 'agePossession', 'furnishing_type', 'luxury_category', 'floor_category']

In [18]:
# Creating a column transformer for preprocessing
preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(),['bedRoom', 'bathroom', 'built_up_area', 'servant room', 'store room']),
        ('cat', OrdinalEncoder(), columns_to_encode)
    ],
    remainder='passthrough'
)


#### Passthrough :-
- In the scikit-learn OrdinalEncoder, the passthrough parameter allows you to include the non-categorical columns in the transformed output without encoding them. When passthrough is set to 'passthrough', the transformer will transform the categorical columns and include the non-categorical columns in the resulting array.




In [19]:
# Creating a pipeline
pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor',LinearRegression())
])

In [20]:
pipeline

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category'])])),
                ('regressor', LinearRegression())])

In [21]:
# K-Fold Cross Validation

kfold = KFold(n_splits=10, shuffle=True, random_state=42)
scores= cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring='r2')

In [22]:
scores.mean(), scores.std()

(0.7363096633436829, 0.03238005754429937)

- So after apply ordinal encoding through pipeline and apply linear regression on X and y data. And do kfold cross validation and check mean of score . 
- It is not so accurate so now again do this by splitting data.


In [23]:
X_train, X_test, y_train, y_test = train_test_split(X,y_transformed, test_size=0.2, random_state=42)

In [24]:
pipeline.fit(X_train, y_train)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category'])])),
                ('regressor', LinearRegression())])

In [25]:
y_pred = pipeline.predict(X_test)

In [26]:
y_pred

array([1.15700081, 0.62935155, 0.78923869, 1.55827521, 1.37806207,
       1.53155016, 2.13474919, 1.23304871, 1.1204441 , 1.11267576,
       1.41235811, 0.71257546, 1.17963125, 0.94687144, 2.82323315,
       0.53201954, 0.61372621, 0.47943071, 0.75822332, 1.45440647,
       0.91377109, 0.80868333, 0.5414655 , 0.57317462, 1.01128127,
       1.23224246, 0.73995281, 0.4814698 , 0.91215684, 1.80808657,
       0.34147627, 0.68461037, 1.31543477, 0.47491893, 0.62086681,
       1.88091792, 0.77551852, 0.55149482, 0.5482935 , 0.38064681,
       0.67804879, 0.82079697, 0.45183075, 1.19277196, 1.19992839,
       0.38720351, 1.74781288, 0.91663109, 0.97387759, 1.1551884 ,
       0.99269947, 0.60040363, 1.54234043, 0.95755836, 0.94013957,
       0.34856039, 2.70521147, 1.67161834, 1.66305621, 1.00936094,
       1.1297326 , 1.2844578 , 0.5637419 , 0.77588884, 0.3702542 ,
       1.03630085, 0.8251405 , 1.62536322, 0.60463535, 1.0252044 ,
       1.13906142, 0.59046895, 0.93467746, 0.9488749 , 1.09670

In [27]:
y_pred = np.expm1(y_pred)

In [28]:
y_pred

array([ 2.18038041,  0.87639344,  1.20171961,  3.75062037,  2.967206  ,
        3.62534131,  7.45492564,  2.4316758 ,  2.06621562,  2.04248847,
        3.1056255 ,  1.03923648,  2.25317437,  1.57763277, 15.83118047,
        0.70236684,  0.84730202,  0.61515464,  1.13448056,  3.28194125,
        1.49370883,  1.24495018,  0.71852351,  0.77388955,  1.74912113,
        2.42891011,  1.09583661,  0.61845146,  1.48968659,  5.0987667 ,
        0.40702321,  0.98299906,  2.72637075,  0.60788384,  0.86054007,
        5.55952323,  1.17171791,  0.73584585,  0.73029775,  0.46323071,
        0.97003004,  1.27231009,  0.571186  ,  2.29620551,  2.31987918,
        0.47285619,  4.74203041,  1.50085103,  1.64819319,  2.17462147,
        1.69850919,  0.8228544 ,  3.6755202 ,  1.60532743,  1.56033874,
        0.41702612, 13.95747943,  4.32077167,  4.27540899,  1.74384698,
        2.09482884,  2.61270861,  0.75723561,  1.1725223 ,  0.44810268,
        1.81877065,  1.28220139,  4.08026393,  0.83058456,  1.78

In [29]:
np.log1p(2.18038041)

1.1570008154236553

In [30]:
# apply MAE (Mean Absolute Error) upon linear regression model
mean_absolute_error(np.expm1(y_test), y_pred)

0.9463822160089359

- Then split data into train test split and apply pipeline on this data then apply prediction after that for checking how much mistake model doing will apply MAE , but as we transformed target data into y_logtransformed in log transformed form, so firstly convert this into original form to check mae error.

## why we need to change in original form for applying mae


- When we apply a log transformation to the target variable, it compresses the scale of the values. This is often done to handle data with a wide range of values or to make the data more symmetric. However, when we calculate metrics like Mean Absolute Error (MAE) on log-transformed data, the result is also in the transformed space.
- For ease of interpretation and communication, it is common to convert the error back to the original scale after the evaluation. This conversion is done using the inverse of the log transformation. The np.expm1 function is used for this purpose.


#### Here's why this conversion is necessary:
1. Interpretability: MAE represents the average absolute error between predicted and actual values. Converting it back to the original scale makes the error values more interpretable and relatable to the original data.
2. Communication: If you're reporting model performance to stakeholders or colleagues, they may be more familiar with the original scale of the target variable. Converting the metric back to the original scale facilitates clear communication.
3. Consistency: When comparing the performance of different models or evaluating against a benchmark, it's essential to have consistent units. Converting the MAE back to the original scale ensures that the metric is in the same units as the original data.
In summary, while you could technically evaluate models on log-transformed data, converting the metrics back to the original scale enhances interpretability and makes it easier to communicate the results.



In [31]:
# creating function to apply all model in one go
def scorer(model_name, model):
    
    output = []
    
    output.append(model_name)
    
    pipeline = Pipeline([
        ('preprocessor', preprocessor),
        ('regressor',model)
    ])
    
    # K fold cross -validation
    kfold = KFold(n_splits=10,shuffle=True, random_state=42)
    scores= cross_val_score(pipeline, X,y_transformed, cv=kfold, scoring='r2')
    
    output.append(scores.mean())
    
    X_train, X_test, y_train, y_test = train_test_split(X, y_transformed, test_size=0.2, random_state=42)
    
    pipeline.fit(X_train,y_train)
    
    y_pred = pipeline.predict(X_test)
    
    y_pred = np.expm1(y_pred)
    
    output.append(mean_absolute_error(np.expm1(y_test),y_pred))
    
    return output

In [32]:
model_dict = {
    'linear_reg':LinearRegression(),
    'svr':SVR(),
    'ridge':Ridge(),
    'LASSO':Lasso(),
    'decision tree': DecisionTreeRegressor(),
    'random forest':RandomForestRegressor(),
    'extra trees': ExtraTreesRegressor(),
    'gradient boosting': GradientBoostingRegressor(),
    'adaboost': AdaBoostRegressor(),
    'mlp': MLPRegressor(),
    'xgboost':XGBRegressor()
}

In [33]:
model_output= []
for model_name, model in model_dict.items():
    model_output.append(scorer(model_name, model))

In [34]:
model_output

[['linear_reg', 0.7363096633436829, 0.9463822160089359],
 ['svr', 0.7642021216646013, 0.8472636473483931],
 ['ridge', 0.7363125343993554, 0.9463387741853388],
 ['LASSO', 0.05943378064493572, 1.528905986892753],
 ['decision tree', 0.7749793548210808, 0.7528905215832021],
 ['random forest', 0.8813910692137075, 0.5319889696545623],
 ['extra trees', 0.8684067793190003, 0.5502562525116986],
 ['gradient boosting', 0.8725427763144094, 0.5752015865215504],
 ['adaboost', 0.7546724167131268, 0.8525485536038616],
 ['mlp', 0.8058278444424157, 0.7100444266164989],
 ['xgboost', 0.8894876835260124, 0.5040475166212824]]

In [35]:
model_df = pd.DataFrame(model_output, columns = ['name', 'r2', 'mae'])

In [36]:
model_df

name        r2       mae
0          linear_reg  0.736310  0.946382
1                 svr  0.764202  0.847264
2               ridge  0.736313  0.946339
3               LASSO  0.059434  1.528906
4       decision tree  0.774979  0.752891
5       random forest  0.881391  0.531989
6         extra trees  0.868407  0.550256
7   gradient boosting  0.872543  0.575202
8            adaboost  0.754672  0.852549
9                 mlp  0.805828  0.710044
10            xgboost  0.889488  0.504048

In [37]:
model_df.sort_values(['mae'])

name        r2       mae
10            xgboost  0.889488  0.504048
5       random forest  0.881391  0.531989
6         extra trees  0.868407  0.550256
7   gradient boosting  0.872543  0.575202
9                 mlp  0.805828  0.710044
4       decision tree  0.774979  0.752891
1                 svr  0.764202  0.847264
8            adaboost  0.754672  0.852549
2               ridge  0.736313  0.946339
0          linear_reg  0.736310  0.946382
3               LASSO  0.059434  1.528906

**conclusion**

- In ordinal encoding, when applied to all models, tree-based models outperformed over linear-based models. 
- Linear models tend to work better with one-hot encoding on categorical features, and the performance improvement was notable. 
- The R2 score increased to approximately 0.88, and the mean absolute error (MAE) reduced from 0.94 to 0.50 on average.


In [38]:
columns_to_encode

['property_type',
 'sector',
 'balcony',
 'agePossession',
 'furnishing_type',
 'luxury_category',
 'floor_category']

In [39]:
X.columns

Index(['property_type', 'sector', 'bedRoom', 'bathroom', 'balcony',
       'agePossession', 'built_up_area', 'servant room', 'store room',
       'furnishing_type', 'luxury_category', 'floor_category'],
      dtype='object')

In [40]:
X['furnishing_type'].value_counts()

furnishing_type
unfurnished      2349
semifurnished    1018
furnished         187
Name: count, dtype: int64

In [41]:
X['luxury_category'].value_counts()

luxury_category
Low       1594
Medium    1465
High       495
Name: count, dtype: int64

In [42]:
X['floor_category'].value_counts()

floor_category
Mid Floor     1797
Low Floor      953
High Floor     804
Name: count, dtype: int64

In [43]:
X['agePossession'].value_counts()

agePossession
Relatively New        1732
Moderately Old         619
New Property           599
Old Property           327
Under Construction     277
Name: count, dtype: int64

In [44]:
X['sector'].value_counts().nunique()

59

In [45]:
columns_to_encode = ['property_type', 'balcony',  'luxury_category', 'floor_category']


# ONE HOT ENCODING

In [46]:
# creting a column transformer for preprocessing 

preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['bedRoom', 'bathroom', 'built_up_area','servant room', 'store room']),
        ('cat',OrdinalEncoder(), columns_to_encode),
        ('cat1', OneHotEncoder(drop='first', sparse_output=False),['sector', 'agePossession', 'furnishing_type'])
    ],
    remainder ='passthrough'

)

- The sparse_output=False parameter in OneHotEncoder specifies that the output should be a dense array instead of a sparse matrix. When sparse_output is set to False, the encoder will return a standard NumPy array instead of a sparse matrix. Sparse matrices are more memory-efficient when dealing with large datasets, but using sparse_output=False can be beneficial when we want a dense array, which is easier to work with in some situations.



In [47]:
# creating a pipeline and apply only regression model

pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor', LinearRegression())
])

In [48]:
# K-fold Cross valdiation

kfold = KFold(n_splits=10,shuffle=True,random_state=42)
scores=cross_val_score(pipeline,X,y_transformed, cv=kfold, scoring='r2')



In [49]:
scores.mean()

0.8546150908270335

In [50]:
scores.std()

0.015992529108130545

- so when applied one hot encoding on required column (sector, age possession, furnishing type) model performance increase

In [51]:
X_train, X_test, y_train, y_test = train_test_split(X,y_transformed,test_size=0.2,random_state=42)

In [52]:
pipeline.fit(X_train,y_train)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'balcony',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['sector', 'agePossession',
                                                   'furnishing_type'])])),
                ('regressor', LinearRegression())])

In [53]:
y_pred= pipeline.predict(X_test)

In [54]:
y_pred # log transformed data

array([0.95948062, 0.44535937, 0.77997416, 1.33069862, 1.29966149,
       1.3916004 , 2.19166473, 1.03917757, 1.02131607, 1.00047059,
       1.34358081, 0.73907334, 1.35087419, 0.92098018, 2.91804296,
       0.51266834, 1.16420001, 0.31023222, 0.6347904 , 1.33201534,
       0.81966241, 0.83101372, 0.58467693, 0.73797   , 1.03899129,
       1.50908752, 0.54337618, 0.5735083 , 0.72627536, 2.17986226,
       0.34732932, 0.46702905, 1.6140592 , 0.33059399, 0.67060976,
       1.62813626, 0.96402316, 0.50927005, 0.43088658, 0.32754343,
       0.51083209, 1.1113612 , 0.42932412, 1.03539775, 1.00065311,
       0.4473248 , 1.84171612, 1.00327454, 1.14759978, 0.97871021,
       0.97150647, 0.50739209, 1.79886834, 1.1529379 , 0.73027039,
       1.00897435, 2.50628507, 1.41952768, 1.77387476, 0.98912987,
       0.95605785, 1.41816826, 0.49276789, 1.46390141, 0.28869516,
       1.03946972, 1.37919669, 1.32195379, 0.43509505, 0.80396113,
       1.35275685, 0.59113845, 1.01965446, 1.11291091, 1.42146

In [55]:
y_pred = np.expm1(y_pred)

In [56]:
y_pred # after conversion in original form

array([ 1.61034037,  0.56105109,  1.1814159 ,  2.78368584,  2.66805479,
        3.02128055,  7.95010023,  1.82689113,  1.77684688,  1.71956131,
        2.83274328,  1.0939942 ,  2.86079913,  1.51175115, 17.50503697,
        0.66974069,  2.20335922,  0.36374176,  0.88662666,  2.78867116,
        1.26973347,  1.29564469,  0.79441117,  1.09168509,  1.82636458,
        3.52260212,  0.7218102 ,  0.77448156,  1.06736606,  7.84508786,
        0.41528273,  0.59524774,  4.02315989,  0.3917946 ,  0.95542931,
        4.09437131,  1.6222249 ,  0.66407606,  0.53862103,  0.38755532,
        0.66667745,  2.03849156,  0.53621888,  1.81622618,  1.72005774,
        0.56412224,  5.30735314,  1.72719753,  2.15062165,  1.66102188,
        1.64192143,  0.66095393,  5.04280517,  2.167485  ,  1.07564177,
        1.74278642, 11.25930294,  3.13516688,  4.89364561,  1.68889376,
        1.60142103,  3.12954926,  0.63684055,  3.32279165,  0.3346848 ,
        1.82771713,  2.97170984,  2.7507424 ,  0.54510992,  1.23

In [57]:
mean_absolute_error(np.expm1(y_test), y_pred)

0.6496724748332862

- so after applying one hot encoding now model giving error of 64 lacs instead of 94 lacs fron older result.

In [58]:
def scorer(model_name, model):
    
    output = []
    
    output.append(model_name)
    
    pipeline = Pipeline([
        ('preprocessor', preprocessor),
        ('regressor', model)
    ])
    
    # K-fold cross validation
    kfold = KFold(n_splits=10, shuffle=True, random_state=42)
    scores= cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring='r2')
    
    
    output.append(scores.mean())
    
    X_train, X_test, y_train, y_test = train_test_split(X, y_transformed, test_size=0.2, random_state=42)
    
    
    pipeline.fit(X_train, y_train)
    
    y_pred = pipeline.predict(X_test)
    
    y_pred= np.expm1(y_pred)
    
    output.append(mean_absolute_error(np.expm1(y_test), y_pred))
    
    return output

In [59]:
model_dict = {
    'linear_reg':LinearRegression(),
    'svr':SVR(),
    'ridge':Ridge(),
    'LASSO':Lasso(),
    'decision tree': DecisionTreeRegressor(),
    'random forest':RandomForestRegressor(),
    'extra trees': ExtraTreesRegressor(),
    'gradient boosting': GradientBoostingRegressor(),
    'adaboost': AdaBoostRegressor(),
    'mlp': MLPRegressor(),
    'xgboost':XGBRegressor()
}

In [60]:
model_output = []

for model_name, model in model_dict.items():
    model_output.append(scorer(model_name, model))

In [61]:
model_output

[['linear_reg', 0.8546150908270335, 0.6496724748332862],
 ['svr', 0.882773714913079, 0.533683181672724],
 ['ridge', 0.8549320280691518, 0.653285879050357],
 ['LASSO', -0.003597657277664901, 1.576391507281618],
 ['decision tree', 0.7921189170838854, 0.6627186619854772],
 ['random forest', 0.8712271521949999, 0.5336264574182039],
 ['extra trees', 0.8865040488180334, 0.4821611284202083],
 ['gradient boosting', 0.8564365889136928, 0.6022901904853727],
 ['adaboost', 0.7229961091717323, 0.9101271005981176],
 ['mlp', 0.8769912814016149, 0.5500112284726353],
 ['xgboost', 0.8859335970032622, 0.4953935434781381]]

In [62]:
model_df = pd.DataFrame(model_output, columns=['name', 'r2', 'mae'])

In [63]:
model_df.sort_values(['mae'])

name        r2       mae
6         extra trees  0.886504  0.482161
10            xgboost  0.885934  0.495394
5       random forest  0.871227  0.533626
1                 svr  0.882774  0.533683
9                 mlp  0.876991  0.550011
7   gradient boosting  0.856437  0.602290
0          linear_reg  0.854615  0.649672
2               ridge  0.854932  0.653286
4       decision tree  0.792119  0.662719
8            adaboost  0.722996  0.910127
3               LASSO -0.003598  1.576392

- as of now extra trees giving best reduce error 48 lakh approx. 

# One Hot Encoding with PCA

In [64]:
# Creating a column transformer for preprocessing
preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['bedRoom', 'bathroom', 'built_up_area', 'servant room', 'store room']),
        ('cat', OrdinalEncoder(), columns_to_encode),
        ('cat1',OneHotEncoder(drop='first',sparse_output=False),['sector','agePossession','furnishing_type'])
    ], 
    remainder='passthrough'
)

In [65]:
# Creating a pipeline
pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('pca', PCA(n_components=0.95)),
    ('regressor', LinearRegression())
])

In [66]:
# K-fold cross-validation
kfold = KFold(n_splits=10, shuffle=True, random_state=42)
scores = cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring='r2')

In [67]:
scores.mean()

0.7644414727636658

In [68]:
scores.std()

0.028840370479173625

In [69]:
def scorer(model_name, model):
    
    output = []
    
    output.append(model_name)
    
    pipeline = Pipeline([
        ('preprocessor', preprocessor),
        ('pca', PCA(n_components=0.95)),
        ('regressor', model)
    ])
    
    #kfold cross-validation
    kfold = KFold(n_splits=10, shuffle=True, random_state=42)
    scores= cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring='r2')
    
    output.append(scores.mean())
    
    X_train, X_test, y_train, y_test = train_test_split(X, y_transformed, test_size=0.2, random_state=42)
    
    pipeline.fit(X_train, y_train)
    
    y_pred = pipeline.predict(X_test)
    
    y_pred = np.expm1(y_pred)
    
    output.append(mean_absolute_error(np.expm1(y_test), y_pred))
    
    return output
    

In [70]:
model_dict = {
    'linear_reg': LinearRegression(),
    'svr': SVR(),
    'ridge': Ridge(),
    'LASSO': Lasso(),
    'decision tree': DecisionTreeRegressor(),
    'random forest': RandomForestRegressor(),
    'extra trees': ExtraTreesRegressor(),
    'gradient boosting': GradientBoostingRegressor(),
    'adaboost': AdaBoostRegressor(),
    'mlp': MLPRegressor(),
    'xgboost': XGBRegressor()
}

In [71]:
model_output = []
for model_name, model in model_dict.items():
    model_output.append(scorer(model_name, model))

/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


In [72]:
model_output

[['linear_reg', 0.7644414727636658, 0.9061825500645796],
 ['svr', 0.8235279034489412, 0.6641942003605255],
 ['ridge', 0.7644856740752288, 0.9062387142737784],
 ['LASSO', -0.003597657277664901, 1.576391507281618],
 ['decision tree', 0.6302618223831079, 0.8379467073682476],
 ['random forest', 0.8232063915826198, 0.6336697655886471],
 ['extra trees', 0.840817693381142, 0.5910350362097101],
 ['gradient boosting', 0.8238266976133148, 0.6943503386956815],
 ['adaboost', 0.6866927111356305, 0.9087473174519237],
 ['mlp', 0.8228039995282769, 0.7070752552222214],
 ['xgboost', 0.81973238047202, 0.614574593402833]]

In [73]:
model_df = pd.DataFrame(model_output, columns=['name', 'r2', 'mae'])

In [74]:
model_df.sort_values(['mae'])

name        r2       mae
6         extra trees  0.840818  0.591035
10            xgboost  0.819732  0.614575
5       random forest  0.823206  0.633670
1                 svr  0.823528  0.664194
7   gradient boosting  0.823827  0.694350
9                 mlp  0.822804  0.707075
4       decision tree  0.630262  0.837947
0          linear_reg  0.764441  0.906183
2               ridge  0.764486  0.906239
8            adaboost  0.686693  0.908747
3               LASSO -0.003598  1.576392

# Target Encoding

- Now, to handle features with high cardinality, such as the 'sector' column, I'll utilize target encoding. Before applying target encoding, it's crucial to split the data into training and testing sets to prevent data leakage. Target encoding involves calculating the average target value for each category in a categorical feature. For instance, if 'sector' 49 appears three times, the algorithm will compute the average price for these occurrences and replace 'sector' 49 with this average value

- Target encoding work best with Tree based Algorithm

In [75]:
!pip install category_encoders

In [76]:
import category_encoders as ce

In [77]:
columns_to_encode = ['property_type', 'sector', 'balcony', 'agePossession', 'furnishing_type', 'luxury_category', 'floor_category']

In [78]:
# creating a column transformer for preprocessing

preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['bedRoom', 'bathroom', 'built_up_area', 'servant room', 'store room']),
        ('cat', OrdinalEncoder(), columns_to_encode),
        ('cat1', OneHotEncoder(drop='first', sparse_output=False),['agePossession']),
        ('target_enc', ce.TargetEncoder(),['sector'])
    ],
    remainder='passthrough'

)

In [79]:
# creating a pipeline

pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor', LinearRegression())
])

In [80]:
# k fold cross validation

kfold = KFold(n_splits=10, shuffle=True, random_state=42)
scores = cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring = 'r2')

In [81]:
scores.mean(), scores.std()

(0.829521918225536, 0.018384463379122876)

In [82]:
def scorer(model_name, model):
    
    output = []
    
    output.append(model_name)
    
    pipeline = Pipeline([
        ('preprocessor', preprocessor),
        ('regressor', model)
    ])
    
    # K fold cross validation
    kfold = KFold(n_splits=10, shuffle=True, random_state=42)
    scores= cross_val_score(pipeline, X, y_transformed, cv=kfold, scoring='r2')
    
    output.append(scores.mean())
    
    X_train, X_test, y_train, y_test = train_test_split(X, y_transformed, test_size=0.2, random_state=42)
    
    pipeline.fit(X_train, y_train)
    
    y_pred = pipeline.predict(X_test)
    
    y_pred = np.expm1(y_pred)
    
    output.append(mean_absolute_error(np.expm1(y_test),y_pred))
    
    return output
    

In [83]:
model_dict = {
    'linear_reg': LinearRegression(),
    'svr':SVR(),
    'ridge':Ridge(),
    'LASSO': Lasso(),
    'decision tree': DecisionTreeRegressor(),
    'random forest': RandomForestRegressor(),
    'extra trees': ExtraTreesRegressor(),
    'gradient boosting': GradientBoostingRegressor(),
    'adaboost': AdaBoostRegressor(),
    'mlp': MLPRegressor(),
    'xgboost': XGBRegressor()
}

In [84]:
model_output = []
for model_name, model in model_dict.items():
    model_output.append(scorer(model_name, model))

In [85]:
model_output

[['linear_reg', 0.829521918225536, 0.7130109838896389],
 ['svr', 0.7829174051174264, 0.8188507474317223],
 ['ridge', 0.8295359700269425, 0.7135228301064991],
 ['LASSO', 0.05943378064493572, 1.528905986892753],
 ['decision tree', 0.8313466587797673, 0.540615143633739],
 ['random forest', 0.900512604078554, 0.4532607686837288],
 ['extra trees', 0.902081478877165, 0.46737342704104196],
 ['gradient boosting', 0.8888946263658445, 0.5106831693611541],
 ['adaboost', 0.817266128663063, 0.6898270672239899],
 ['mlp', 0.8481947048381254, 0.6201079787009965],
 ['xgboost', 0.9047983252719011, 0.4475181196963234]]

In [86]:
model_df = pd.DataFrame(model_output , columns = ['name', 'r2', 'mae'])

In [87]:
model_df.sort_values(['mae'])

name        r2       mae
10            xgboost  0.904798  0.447518
5       random forest  0.900513  0.453261
6         extra trees  0.902081  0.467373
7   gradient boosting  0.888895  0.510683
4       decision tree  0.831347  0.540615
9                 mlp  0.848195  0.620108
8            adaboost  0.817266  0.689827
0          linear_reg  0.829522  0.713011
2               ridge  0.829536  0.713523
1                 svr  0.782917  0.818851
3               LASSO  0.059434  1.528906

# Hyperparameter Tuning

In [124]:
from sklearn.model_selection import GridSearchCV

In [125]:
param_grid = {
    'regressor__n_estimators':[50,100,200,300],
    'regressor__max_depth':[None, 10,20,30],
    'regressor__max_samples':[0.1,0.25,0.5,1.0],
    'regressor__max_features':['auto', 'sqrt']
}

In [126]:
columns_to_encode = ['property_type', 'sector', 'balcony', 'agePossession', 'furnishing_type', 'luxury_category', 'floor_category']

        

In [127]:
# Creating a column transformer for preprocessing
preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['bedRoom', 'bathroom', 'built_up_area', 'servant room', 'store room']),
        ('cat', OrdinalEncoder(), columns_to_encode),
        ('cat1',OneHotEncoder(drop='first',sparse_output=False),['agePossession']),
        ('target_enc', ce.TargetEncoder(), ['sector'])
    ], 
    remainder='passthrough'
)

In [128]:
pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor', RandomForestRegressor())
])

In [129]:
kfold = KFold(n_splits=10, shuffle=True, random_state=42)

In [130]:
search = GridSearchCV(pipeline, param_grid, cv=kfold, scoring='r2', n_jobs=-1, verbose=4)

In [131]:
search.fit(X, y_transformed)

Fitting 10 folds for each of 128 candidates, totalling 1280 fits


/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
/Users/nimishasingh/anaconda3/lib/python3.11/site-packages/pandas/core/arrays/masked

GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=Pipeline(steps=[('preprocessor',
                                        ColumnTransformer(remainder='passthrough',
                                                          transformers=[('num',
                                                                         StandardScaler(),
                                                                         ['bedRoom',
                                                                          'bathroom',
                                                                          'built_up_area',
                                                                          'servant '
                                                                          'room',
                                                                          'store '
                                                                          'room']),
                                                                        ('cat',
                                                                         OrdinalEncoder(),
                                                                         ['property_type',
                                                                          'sector',
                                                                          'balcony',
                                                                          'agePossession',
                                                                          'furnishing_type',...
                                                                         OneHotEncoder(drop='first',
                                                                                       sparse_output=False),
                                                                         ['agePossession']),
                                                                        ('target_enc',
                                                                         TargetEncoder(),
                                                                         ['sector'])])),
                                       ('regressor', RandomForestRegressor())]),
             n_jobs=-1,
             param_grid={'regressor__max_depth': [None, 10, 20, 30],
                         'regressor__max_features': ['auto', 'sqrt'],
                         'regressor__max_samples': [0.1, 0.25, 0.5, 1.0],
                         'regressor__n_estimators': [50, 100, 200, 300]},
             scoring='r2', verbose=4)

In [132]:
final_pipe = search.best_estimator_

In [133]:
final_pipe

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['agePossession']),
                                                 ('target_enc', TargetEncoder(),
                                                  ['sector'])])),
                ('regressor',
                 RandomForestRegressor(max_depth=20, max_features='sqrt',
                                       max_samples=1.0, n_estimators=200))])

In [134]:
search.best_params_

{'regressor__max_depth': 20,
 'regressor__max_features': 'sqrt',
 'regressor__max_samples': 1.0,
 'regressor__n_estimators': 200}

In [135]:
final_pipe = search.best_estimator_

In [136]:
search.best_params_

{'regressor__max_depth': 20,
 'regressor__max_features': 'sqrt',
 'regressor__max_samples': 1.0,
 'regressor__n_estimators': 200}

In [137]:
search.best_score_

0.9028481009974498

In [138]:
final_pipe.fit(X,y_transformed)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['agePossession']),
                                                 ('target_enc', TargetEncoder(),
                                                  ['sector'])])),
                ('regressor',
                 RandomForestRegressor(max_depth=20, max_features='sqrt',
                                       max_samples=1.0, n_estimators=200))])

In [139]:
final_pipe 

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['agePossession']),
                                                 ('target_enc', TargetEncoder(),
                                                  ['sector'])])),
                ('regressor',
                 RandomForestRegressor(max_depth=20, max_features='sqrt',
                                       max_samples=1.0, n_estimators=200))])

In [140]:
final_pipe.fit(X,y_transformed)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['agePossession']),
                                                 ('target_enc', TargetEncoder(),
                                                  ['sector'])])),
                ('regressor',
                 RandomForestRegressor(max_depth=20, max_features='sqrt',
                                       max_samples=1.0, n_estimators=200))])

# Exporting the Model

In [142]:
preprocessor = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), ['bedRoom', 'bathroom', 'built_up_area', 'servant room', 'store room']),
        ('cat', OrdinalEncoder(), columns_to_encode),
        ('cat1',OneHotEncoder(drop='first',sparse_output=False),['sector','agePossession'])
    ], 
    remainder='passthrough'
)

In [141]:
columns_to_encode

['property_type',
 'sector',
 'balcony',
 'agePossession',
 'furnishing_type',
 'luxury_category',
 'floor_category']

In [143]:
pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('regressor', RandomForestRegressor(n_estimators=500))
])

In [144]:
pipeline.fit(X,y_transformed)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(remainder='passthrough',
                                   transformers=[('num', StandardScaler(),
                                                  ['bedRoom', 'bathroom',
                                                   'built_up_area',
                                                   'servant room',
                                                   'store room']),
                                                 ('cat', OrdinalEncoder(),
                                                  ['property_type', 'sector',
                                                   'balcony', 'agePossession',
                                                   'furnishing_type',
                                                   'luxury_category',
                                                   'floor_category']),
                                                 ('cat1',
                                                  OneHotEncoder(drop='first',
                                                                sparse_output=False),
                                                  ['sector',
                                                   'agePossession'])])),
                ('regressor', RandomForestRegressor(n_estimators=500))])

[CV 8/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 10/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.2s
[CV 9/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 2/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 8/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 3/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 6/10] END regressor__max_depth=None, regressor__m

[CV 4/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 5/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 1/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 9/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 9/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 7/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 2/10] END regressor__max_depth=None, regressor__m

[CV 2/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 3/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.2s
[CV 4/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 1/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 5/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 5/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 3/10] END regressor__max_depth=None, regressor__m

[CV 1/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 4/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 8/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 6/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.2s
[CV 7/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 8/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 5/10] END regressor__max_depth=None, regressor__m

[CV 7/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 1/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.2s
[CV 2/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 8/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 6/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 1/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 9/10] END regressor__max_depth=None, regressor__m

[CV 5/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 2/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.2s
[CV 3/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 7/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 10/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.1s
[CV 6/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 4/10] END regressor__max_depth=None, regressor__

[CV 3/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 6/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 7/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 5/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.2s
[CV 3/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.2s
[CV 2/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 10/10] END regressor__max_depth=None, regressor__

[CV 6/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 9/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=50;, score=nan total time=   0.2s
[CV 10/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=100;, score=nan total time=   0.1s
[CV 10/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=200;, score=nan total time=   0.1s
[CV 4/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.1, regressor__n_estimators=300;, score=nan total time=   0.2s
[CV 4/10] END regressor__max_depth=None, regressor__max_features=auto, regressor__max_samples=0.25, regressor__n_estimators=50;, score=nan total time=   0.1s
[CV 1/10] END regressor__max_depth=None, regressor__

In [145]:
import pickle

with open('pipeline.pkl', 'wb') as file:
    pickle.dump(pipeline, file)

In [146]:
with open('df.pkl', 'wb') as file:
    pickle.dump(X, file)

In [147]:
X

property_type             sector  bedRoom  bathroom balcony  \
0             flat          sector 36      3.0       2.0       2   
1             flat          sector 89      2.0       2.0       2   
2             flat         sohna road      2.0       2.0       1   
3             flat          sector 92      3.0       4.0      3+   
4             flat         sector 102      2.0       2.0       1   
5             flat        gwal pahari      4.0       4.0      3+   
6             flat         sector 108      3.0       3.0      3+   
7             flat         sector 102      3.0       4.0       3   
8            house         sector 105      3.0       2.0       1   
9            house          sector 26      3.0       3.0       2   
10           house         sector 109      3.0       2.0       0   
11            flat          sector 28      2.0       2.0       2   
12            flat         sector 109      3.0       4.0       3   
13            flat          sector 65      4.0       4.0      3+   
14           house          sector 12      2.0       4.0       2   
15            flat          sector 92      3.0       4.0       3   
16            flat          sector 85      2.0       2.0       3   
17            flat         sector 70a      2.0       2.0       3   
18            flat          sector 85      3.0       4.0      3+   
19            flat          sector 30      2.0       2.0       1   
20            flat         sector 107      2.0       2.0      3+   
21            flat           sector 3      2.0       2.0       3   
22            flat           sector 2      1.0       1.0       1   
23           house          sector 41      8.0       5.0      3+   
24           house          sector 41      7.0       7.0      3+   
25            flat          sector 28      4.0       2.0      3+   
26           house           sector 4      1.0       1.0       0   
27           house         sector 109      4.0       4.0      3+   
28            flat          sector 62      2.0       2.0       3   
29           house          sector 49      6.0       6.0       3   
30            flat          sector 81      2.0       2.0       3   
31            flat          sector 65      3.0       3.0       3   
32            flat          sector 66      3.0       3.0       3   
33           house          sector 89      2.0       2.0       2   
34            flat          sector 86      3.0       3.0      3+   
35           house          sector 48      4.0       4.0      3+   
36           house         sector 109      5.0       6.0      3+   
37            flat          sector 51      4.0       4.0       3   
38            flat          sector 37      3.0       3.0       3   
39            flat         sector 111      2.0       2.0       2   
40            flat          sector 67      3.0       3.0       3   
41           house          sector 28      4.0       3.0       3   
42            flat         sector 111      3.0       4.0       2   
43            flat         sector 113      3.0       3.0      3+   
44           house          sector 13      3.0       6.0       2   
45            flat          sector 61      3.0       2.0       3   
46            flat         sector 113      3.0       3.0       3   
47            flat          sector 69      3.0       3.0       1   
48            flat          sector 89      3.0       2.0       0   
49            flat         sector 67a      3.0       4.0       3   
50            flat         sector 37d      2.0       2.0       3   
51            flat          sector 82      2.0       2.0       2   
52            flat          sector 53      3.0       3.0      3+   
53            flat          sector 74      2.0       2.0       3   
54            flat         sector 37d      3.0       3.0       3   
55            flat         sector 108      3.0       4.0       3   
56            flat          sector 52      1.0       1.0       0   
57            flat          sector 12      2.0       2.0     

# Trying out the prediction on new data

In [148]:
X.columns

Index(['property_type', 'sector', 'bedRoom', 'bathroom', 'balcony',
       'agePossession', 'built_up_area', 'servant room', 'store room',
       'furnishing_type', 'luxury_category', 'floor_category'],
      dtype='object')

In [149]:
X.iloc[0].values

array(['flat', 'sector 36', 3.0, 2.0, '2', 'New Property', 850.0, 0.0,
       0.0, 'unfurnished', 'Low', 'Low Floor'], dtype=object)

In [150]:
data = [['house', 'sector 102', 4, 3, '3+', 'New Property', 2750, 0, 0, 'unfurnished', 'Low', 'Low Floor']]
columns = ['property_type', 'sector', 'bedRoom', 'bathroom', 'balcony',
       'agePossession', 'built_up_area', 'servant room', 'store room',
       'furnishing_type', 'luxury_category', 'floor_category']

# Convert to DataFrame
one_df = pd.DataFrame(data, columns=columns)

one_df


property_type      sector  bedRoom  bathroom balcony agePossession  \
0         house  sector 102        4         3      3+  New Property   

   built_up_area  servant room  store room furnishing_type luxury_category  \
0           2750             0           0     unfurnished             Low   

  floor_category  
0      Low Floor

In [151]:
np.expm1(pipeline.predict(one_df))

array([3.06614072])

In [154]:
data = [['house', 'sector 49', 3, 3, '3+', 'New Property', 1650, 1, 0, 'unfurnished', 'Low', 'Mid Floor']]
columns = ['property_type', 'sector', 'bedRoom', 'bathroom', 'balcony',
       'agePossession', 'built_up_area', 'servant room', 'store room',
       'furnishing_type', 'luxury_category', 'floor_category']

# Convert to DataFrame
one_df = pd.DataFrame(data, columns=columns)

one_df


property_type     sector  bedRoom  bathroom balcony agePossession  \
0         house  sector 49        3         3      3+  New Property   

   built_up_area  servant room  store room furnishing_type luxury_category  \
0           1650             1           0     unfurnished             Low   

  floor_category  
0      Mid Floor

In [155]:
np.expm1(pipeline.predict(one_df))

array([2.63323361])

In [158]:
data = [['flat', 'sector 49', 3, 3, '3+', 'New Property', 1650, 1, 0, 'unfurnished', 'High', 'Mid Floor']]
columns = ['property_type', 'sector', 'bedRoom', 'bathroom', 'balcony',
       'agePossession', 'built_up_area', 'servant room', 'store room',
       'furnishing_type', 'luxury_category', 'floor_category']

# Convert to DataFrame
one_df = pd.DataFrame(data, columns=columns)

one_df


property_type     sector  bedRoom  bathroom balcony agePossession  \
0          flat  sector 49        3         3      3+  New Property   

   built_up_area  servant room  store room furnishing_type luxury_category  \
0           1650             1           0     unfurnished            High   

  floor_category  
0      Mid Floor

In [159]:
np.expm1(pipeline.predict(one_df))

array([1.95395402])